# Using Symbolic Math to Understand Dynamics of Natural Selection Model

**Table of contents**
 * [Example code for codominant selection](#section1)
 * [Exercises](#section2)
  * [$A_{2}$ dominant](#type1)
    * [$A_{2}$ advantageous](#type1a)
    * [$A_{2}$ deleterious](#type1b)
  * [$A_{2}$ recessive](#type2)
    * [$A_{2}$ advantageous](#type2a)
    * [$A_{2}$ deleterious](#type2b)
  * [Overdominance](#type3)
  * [Underdominance](#type4)

<a id="section1"></a>

## Example code for codominant selection

For this lab, we will use symbolic math with the Python package [SymPy](http://docs.sympy.org/dev/index.html) to find the fixed points and their stability for the model

$$q_{t+1} = F(q_{t}) = \frac{w_{12}q_{t}(1-q_{t}) + w_{22}q_{t}^2}{w_{11}(1-q_{t})^2 + 2w_{12}q_{t}(1-q_{t}) + w_{22}q_{t}^2}$$

To begin, we need to first load the SymPy package into the workspace.

In [2]:
from sympy import *

The next step is to use the `var` command to create symbolic variables.  We will need $q, w_{11}, w_{12}, w_{22}, s$ and $t$.  After this command, we will specify the function $F$.

In [3]:
q,w12,w22,w11,s,t = var('q,w12,w22,w11,s,t')
F = ((w12*(1-q)*q + w22*q*q)/((1-q)*(1-q)*w11 + 2*w12*(1-q)*q + w22*q*q))
F

(q**2*w22 + q*w12*(-q + 1))/(q**2*w22 + 2*q*w12*(-q + 1) + w11*(-q + 1)**2)

Now we will create a dictionary relating the weights as functions of $s$ and possibly $t$.  We'll start with **codominance** for this walkthrough.

In [4]:
selection_type = {w11: 1, w12: 1+s, w22: 1+2*s}

To make things easier, let's go ahead and simplify $F$ by substituting the correct values for the weights (given our choice of selection).  We do that using the `subs` command as follows:

In [5]:
F = F.subs(selection_type)
F

(q**2*(2*s + 1) + q*(-q + 1)*(s + 1))/(q**2*(2*s + 1) + 2*q*(-q + 1)*(s + 1) + (-q + 1)**2)

Note that `**` means _exponent_, i.e. `q**2` is the same as $q^2$.   Let's also try and simplify this expression, which we can do using the `simplify` command.

In [6]:
F = F.simplify()
F

q*(q*s + s + 1)/(2*q*s + 1)

That's better.  To compute fixed points for this system, we need to `solve` for $q$ in the equation

$$F(q) = q$$

which is equivalent to 

$$F(q)-q = 0.$$

In [7]:
fps = solve(F-q,q)
print "These are the fixed points:"
print fps

These are the fixed points:
[0, 1]


Okay, so we've got two fixed points: $q_{\infty} = 0$ and $q_{\infty} = 1$.  Our job now is to compute the stability of these fixed points.  First thing we need to do is compute the (symbolic) derivative $F^{\prime}(q)$.  We do that using the `diff` function.  The first argument to the function is $F$, and the second argument specifies wich variable to take a derivative with respect to.  We only have one variable $q$, so we'll specify that one.

In [8]:
dF = diff(F,q)
dF

q*s/(2*q*s + 1) - 2*q*s*(q*s + s + 1)/(2*q*s + 1)**2 + (q*s + s + 1)/(2*q*s + 1)

Holy smokes!  That is complicated.  Let's use the simplify command again.

In [9]:
dF = dF.simplify()
dF

(2*q**2*s**2 + 2*q*s + s + 1)/(4*q**2*s**2 + 4*q*s + 1)

Uh, I guess that's better?  It's time now to substitute specific values for $q$ for the two fixed points.

In [10]:
dF_q0 = dF.subs(q,0).simplify()
dF_q1 = dF.subs(q,1).simplify()
print "dF/dq at q=0: ", dF_q0
print "dF/dq at q=1: ", dF_q1

dF/dq at q=0:  s + 1
dF/dq at q=1:  (s + 1)/(2*s + 1)


So our question now is: If allele $A_{2}$ has a selective advantage (i.e. $s > 0$), what is the stability of the fixed points?  Remember we have the following stability criteria:

$$
\begin{align}
\textrm{stable}: & \ |F^{\prime}(q_{\infty})| < 1 \\
\textrm{unstable}: & \ |F^{\prime}(q_{\infty})| > 1 \\
\textrm{neutral}: & \ |F^{\prime}(q_{\infty})| = 1
\end{align}
$$

From our results above, we see that

$$
\begin{align}
|F^{\prime}(0)| = |s+1| > 1 & \Rightarrow \textrm{$q_{\infty} = 0$ is unstable} \\
|F^{\prime}(1)| = \left|\frac{s+1}{2s+1}\right| < 1 & \Rightarrow \textrm{$q_{\infty} = 1$ is stable}
\end{align}
$$

In case the first derivative is 1, in which case we are uncertain of stability, we can compute the second derivative and substitute the appropriate $q$ value.

In [11]:
ddF = diff(dF,q)
ddF_q0 = ddF.subs(q,1).simplify()
print "Here is the second derivative, in case the first derivative equals 1:", ddF_q0

Here is the second derivative, in case the first derivative equals 1: -2*s/(4*s**2 + 4*s + 1)


<a id="section2"></a>

## Exercises

Repeat for all selection types under each condition, listed again here for convenience:

Type of selection | $w_{11}$ | $w_{12}$ | $w_{22}$ | Conditions
----------------- | -------- | -------- | -------- | ----------
$A_{2}$ dominant | 1 | 1+s | 1+s | $s > 0$ (advantageous), $s < 0$ (deleterious)
$A_{2}$ recessive | 1 | 1 | 1+s | $s > 0$ (advantageous), $s < 0$ (deleterious)
Overdominance | 1 | 1+s | 1+t | $s > 0$ and $s > t$
Underdominance | 1 | 1+s | 1+t | $s < 0$ and $s < t$

For each of the types listed above, it may be helpful to use the visualization at http://mathinsight.org/cobwebbing_graphical_solution to gain insight into the system and verify your results.

<a id="type1"></a>

### $A_{2}$ dominant

<a id="type1a"></a>

#### $A_{2}$ advantageous

<a id="type1b"></a>

#### $A_{2}$ deleterious

<a id="type2"></a>

### $A_{2}$ recessive

<a id="type2a"></a>

#### $A_{2}$ advantageous

<a id="type2b"></a>

#### $A_{2}$ deleterious

<a id="type3"></a>

### Overdominance

<a id="type4"></a>

### Underdominance